In [99]:
%pip install --upgrade requests
%pip install jieba
%pip install pypinyin
%pip install -v torch torchtext --index-url https://download.pytorch.org/whl/cu118
%pip install chardet
%pip install transformers
%pip install ipywidgets
%pip install --upgrade jupyter_core jupyter_client
%pip install pandas
%pip install re
%pip install scikit-learn
%pip install scipy==1.10.1
%pip install gensim

Using pip 23.1.2 from /usr/local/lib/python3.10/dist-packages/pip (python 3.10)
Looking in indexes: https://download.pytorch.org/whl/cu118
  Using cached jupyter_client-7.4.9-py3-none-any.whl (133 kB)
  Attempting uninstall: jupyter-client
    Found existing installation: jupyter_client 8.6.2
    Uninstalling jupyter_client-8.6.2:
      Successfully uninstalled jupyter_client-8.6.2
  Using cached jupyter_client-8.6.2-py3-none-any.whl (105 kB)
  Attempting uninstall: jupyter_client
    Found existing installation: jupyter_client 7.4.9
    Uninstalling jupyter_client-7.4.9:
      Successfully uninstalled jupyter_client-7.4.9
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
notebook 6.5.5 requires jupyter-client<8,>=5.3.4, but you have jupyter-client 8.6.2 which is incompatible.
ERROR: Could not find a version that satisfies the requirement re (from versions: none)

In [100]:
!jupyter nbextension enable --py widgetsnbextension
import jieba
import pypinyin
import torch
from transformers import AutoTokenizer, AutoModel
import pandas
import re
from sklearn.model_selection import train_test_split
from sklearn.datasets import load_iris
import numpy

Enabling notebook extension jupyter-js-widgets/extension...
Paths used for configuration of notebook: 
    	/root/.jupyter/nbconfig/notebook.json
Paths used for configuration of notebook: 
    	
      - Validating: OK
Paths used for configuration of notebook: 
    	/root/.jupyter/nbconfig/notebook.json


In [101]:
print(torch.cuda.is_available())
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

True


In [102]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


## Normalizacja wejścia - pozbycie się spacji i znaków innych niż chińskie (interpunkcyjnych).
### TODO - przepisać używając słownika znaków chińskich?

In [103]:
# lower() - male litery
# strip() - bez krancowych znakow niedrukowalnych
# bez znakow interpunkcyjnych
def normalizeString(s):
    s = s.lower().strip()
    s = re.sub(r"([.!?])", r"", s)
    s = re.sub(r"([,;:-])", r"", s)
    s = re.sub(r"([。，？”“《》·、！：；π…ㄚ])", r"", s)
    s = re.sub(r"([/])", r"", s)
    s = re.sub(r"(['\"])", r" ", s)
    return s.strip()

def normalizeChinese(s):
    s = normalizeString(s)
    pom = ""
    for c in s:
        if c != " ":
            pom+=c
        #pom+=" "
    return pom.strip()

## Wczytanie zbioru danych. https://www.kaggle.com/datasets/marquis03/chinese-couplets-dataset

In [104]:
fixed_couplets_in = pandas.read_csv("fixed_couplets_in.txt", sep="\t", names=["in"], header=None)
fixed_couplets_out = pandas.read_csv("fixed_couplets_out.txt", sep="\t", names=["out"], header=None)

normalized_fixed_couplets_in=[]
for _ in fixed_couplets_in["in"]:
    normalized_fixed_couplets_in.append(normalizeChinese(_))
normalized_fixed_couplets_out=[]
for _ in fixed_couplets_out["out"]:
    normalized_fixed_couplets_out.append(normalizeChinese(_))

print(normalized_fixed_couplets_in[0])
print(normalized_fixed_couplets_out[0])

腾飞上铁锐意改革谋发展勇当千里马
和谐南供安全送电保畅通争做领头羊


In [105]:
fixed_couplets = pandas.DataFrame(
    {"in": normalized_fixed_couplets_in,
     "out": normalized_fixed_couplets_out
    }
    )
print(fixed_couplets)

                      in               out
0       腾飞上铁锐意改革谋发展勇当千里马  和谐南供安全送电保畅通争做领头羊
1                风弦未拨心先乱           夜幕已沉梦更闲
2                花梦粘于春袖口           莺声溅落柳枝头
3                晋世文章昌二陆           魏家词赋重三曹
4                一句相思吟岁月           千杯美酒醉风情
...                  ...               ...
744910           半榻诗书盈陋室           一墙字画靓寒庐
744911           借角青山埋姓字           掬壶明月洗尘心
744912      苑内尽天姿锦窠仙髻无双艳      亭前多国色金粉紫檀第一香
744913         浩淼洞庭极目天为界         安闲钓叟静心孰羡鱼
744914           志踏云梯能揽月           坚磨铁棒可成针

[744915 rows x 2 columns]


### Odrzucenie 95% danych - więcej niż 5% zajmuje całą pamięć i wywala program.
### Podział danych na zbiór treningowy i testowy.

In [106]:
male, duze = train_test_split(fixed_couplets,test_size=0.99,random_state=42)
treningowe, testowe = train_test_split(male,test_size=0.2,random_state=42)
print(treningowe)
print(testowe)

                       in                out
567354              宇高炎暑净              秋爽飒风来
118920              忧乐关天下              安危系一身
738591            一盏相思量寂寞            三分惆怅兑凄凉
509346  孝驻锦绣城喜吕梁歌飞春融三晋千秋画  义圆和谐梦看汾河景瑞水起九州万卷诗
75388             春临八桂海豚舞            福满九州彩凤飞
...                   ...                ...
116492  创中华古老文明当同日月齐辉功垂万代  启黎庶鸿蒙草昧是与山河并寿德颂千秋
91658         纠缠海角指相思何时作罢        浪迹天涯心倦怠哪处归依
101376       特地显英灵化被逢人歌泽渥       配天昭厚德恩深无处不波恬
262048        温暖鹅城展翅奋飞中国梦        祥和蛇岁铺春欢庆小康年
415192       百业一支歌歌伴和风谐雨唱       九江千古梦梦同朗月艳阳圆

[5959 rows x 2 columns]
                in         out
274864     林霭渐浓迷古寺     尘烟已远隐青山
222320     自古青天匡正义     而今华夏振雄风
100260  真心请客就该一五一五  假意为情何必我开我开
435928     爱本有心今不见     人如无欲意何求
446991     欲抹闲愁实不易     谁将片语问何求
...            ...         ...
213030     万象随缘观自在     一心发愿待君归
299155     春联妙句动心魄     小院雅风入彩光
643294     梅亭吹雪横霜笛     松麓邀云放月筝
628861     红似桃花白似雪     绿如李叶亮如霜
566605     数字双音分两用     联文对句限孤平

[1490 rows x 2 columns]


### Przywrócenie numeracji od 0.

In [107]:
treningowe = treningowe.reset_index(drop=True)
testowe = testowe.reset_index(drop=True)
print(treningowe)
print(testowe)

                     in                out
0                 宇高炎暑净              秋爽飒风来
1                 忧乐关天下              安危系一身
2               一盏相思量寂寞            三分惆怅兑凄凉
3     孝驻锦绣城喜吕梁歌飞春融三晋千秋画  义圆和谐梦看汾河景瑞水起九州万卷诗
4               春临八桂海豚舞            福满九州彩凤飞
...                 ...                ...
5954  创中华古老文明当同日月齐辉功垂万代  启黎庶鸿蒙草昧是与山河并寿德颂千秋
5955        纠缠海角指相思何时作罢        浪迹天涯心倦怠哪处归依
5956       特地显英灵化被逢人歌泽渥       配天昭厚德恩深无处不波恬
5957        温暖鹅城展翅奋飞中国梦        祥和蛇岁铺春欢庆小康年
5958       百业一支歌歌伴和风谐雨唱       九江千古梦梦同朗月艳阳圆

[5959 rows x 2 columns]
              in         out
0        林霭渐浓迷古寺     尘烟已远隐青山
1        自古青天匡正义     而今华夏振雄风
2     真心请客就该一五一五  假意为情何必我开我开
3        爱本有心今不见     人如无欲意何求
4        欲抹闲愁实不易     谁将片语问何求
...          ...         ...
1485     万象随缘观自在     一心发愿待君归
1486     春联妙句动心魄     小院雅风入彩光
1487     梅亭吹雪横霜笛     松麓邀云放月筝
1488     红似桃花白似雪     绿如李叶亮如霜
1489     数字双音分两用     联文对句限孤平

[1490 rows x 2 columns]


### Pakiet *pypinyin* przewiduje wymowę pinyin dobrze bez potrzeby używania pakietu *jieba*.

In [108]:
from pypinyin import pinyin, lazy_pinyin, Style

zdanie = treningowe["in"][4]
print(zdanie)
print(pinyin(zdanie, style=Style.TONE3, neutral_tone_with_five=True))
print(lazy_pinyin(zdanie, style=Style.TONE3, neutral_tone_with_five=True))

slowa = list(jieba.cut(zdanie))
print(slowa)
print(pinyin(slowa, style=Style.TONE3, neutral_tone_with_five=True))
print(lazy_pinyin(slowa, style=Style.TONE3, neutral_tone_with_five=True))

春临八桂海豚舞
[['chun1'], ['lin2'], ['ba1'], ['gui4'], ['hai3'], ['tun2'], ['wu3']]
['chun1', 'lin2', 'ba1', 'gui4', 'hai3', 'tun2', 'wu3']
['春临', '八桂', '海豚', '舞']
[['chun1'], ['lin2'], ['ba1'], ['gui4'], ['hai3'], ['tun2'], ['wu3']]
['chun1', 'lin2', 'ba1', 'gui4', 'hai3', 'tun2', 'wu3']


## Podział wymowy pinyin na początki (initials), końcówki (finals) i tony.
### Zamina w liczby przy pomocy słownika.

In [109]:
from pypinyin.contrib.tone_convert import to_finals, to_initials
# 声母表
_INITIALS=['b','p','m','f','d','t','n','l','g','k','h','j','q','x','zh','ch','sh','r','z','c','s',]
# 声母表,把 y,w 也当作声母
_INITIALS_NOT_STRICT=_INITIALS+['y','w']
# 韵母表
_FINALS=['i','u','ü','a','ia','ua','o','uo','e','ie','üe','ai','uai','ei','uei','ao','iao','ou','iou','an','ian','uan','üan','en','in','uen','ün','ang','iang','uang','eng','ing','ueng','ong','iong','er','ê',]

slownik_initials = {}
licznik = 1
for indeks_wersu_pierwszego in _INITIALS+[""]:
    slownik_initials[indeks_wersu_pierwszego] = licznik
    licznik+=1

slownik_finals = {}
licznik = 1
for indeks_wersu_pierwszego in _FINALS+[""]:
    slownik_finals[indeks_wersu_pierwszego] = licznik
    licznik+=1

def poczatek_koniec_ton(zapis_pinyin_3):
    poczatek = slownik_initials[to_initials(zapis_pinyin_3)]
    koniec = slownik_finals[to_finals(zapis_pinyin_3).replace('v', 'ü')]
    ton = int(zapis_pinyin_3[-1])
    return poczatek, koniec, ton

def wymowy_i_tony_zdania(zdanie):
    zapis_pinyin_3_zdania = lazy_pinyin(zdanie, style=Style.TONE3, neutral_tone_with_five=True)
    poczatki = []
    konce =[]
    tony = []
    # print(zdanie, zapis_pinyin_3_zdania)
    for zp3 in zapis_pinyin_3_zdania:
        p,k,t = poczatek_koniec_ton(zp3)
        poczatki.append(p)
        konce.append(k)
        tony.append(t)
    return poczatki, konce, tony

def dopasuj_dlugosc_wektora(wektor, dlugosc_wektora):
    if len(wektor)>dlugosc_wektora:
        wynik = wektor[:dlugosc_wektora]
    else:
        wynik = numpy.pad(wektor,(0,dlugosc_wektora-len(wektor)), mode='constant', constant_values=0)
    return wynik

In [110]:
def poczatki_konce_tony_dla_zdan(zdania, liczba_wejscia):
    poczatki_wyn = []
    konce_wyn = []
    tony_wyn = []

    for zdanie in zdania:
        poczatki, konce, tony = wymowy_i_tony_zdania(zdanie)

        poczatki = dopasuj_dlugosc_wektora(poczatki, liczba_wejscia)
        konce = dopasuj_dlugosc_wektora(konce, liczba_wejscia)
        tony = dopasuj_dlugosc_wektora(tony, liczba_wejscia)

        poczatki_wyn.append(poczatki)
        konce_wyn.append(konce)
        tony_wyn.append(tony)

    return poczatki_wyn, konce_wyn, tony_wyn

### Początki, końcówki i tony wierszy treningowych.

In [111]:
print(len(treningowe["in"]))
print(treningowe["in"][0])
print(lazy_pinyin(treningowe["in"][0], style=Style.TONE3, neutral_tone_with_five=True))
print(treningowe["out"][0])
print(lazy_pinyin(treningowe["out"][0], style=Style.TONE3, neutral_tone_with_five=True))

liczba_wejscia = 35

poczatki_treningowe_in, konce_treningowe_in, tony_treningowe_in = poczatki_konce_tony_dla_zdan(treningowe["in"], liczba_wejscia)
poczatki_treningowe_out, konce_treningowe_out, tony_treningowe_out = poczatki_konce_tony_dla_zdan(treningowe["out"], liczba_wejscia)

print(len(poczatki_treningowe_in))
print(poczatki_treningowe_in[0])
print(konce_treningowe_in[0])
print(tony_treningowe_in[0])
print(poczatki_treningowe_out[0])
print(konce_treningowe_out[0])
print(tony_treningowe_out[0])

5959
宇高炎暑净
['yu3', 'gao1', 'yan2', 'shu3', 'jing4']
秋爽飒风来
['qiu1', 'shuang3', 'sa4', 'feng1', 'lai2']
5959
[22  9 22 17 12  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
  0  0  0  0  0  0  0  0  0  0  0]
[ 3 16 21  2 32  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
  0  0  0  0  0  0  0  0  0  0  0]
[3 1 2 3 4 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0]
[13 17 21  4  8  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
  0  0  0  0  0  0  0  0  0  0  0]
[19 30  4 31 12  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
  0  0  0  0  0  0  0  0  0  0  0]
[1 3 4 1 2 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0]


## Zanurzenia BAAI wierszy treningowych. https://huggingface.co/BAAI/bge-small-zh-v1.5

In [112]:
# # Load model from HuggingFace Hub
# tokenizer = AutoTokenizer.from_pretrained("BAAI/bge-small-zh-v1.5")
# model = AutoModel.from_pretrained("BAAI/bge-small-zh-v1.5")
# model.eval()

# def zanurzenia_zdan(lista_zdan):
#     # Sentences we want sentence embeddings for
#     #sentences = ["样例数据-1样例数据", "样例数据-2样例数据"]
#     sentences = lista_zdan

#     # Tokenize sentences
#     encoded_input = tokenizer(sentences, padding=True, truncation=True, return_tensors='pt')
#     # for s2p(short query to long passage) retrieval task, add an instruction to query (not add instruction for passages)
#     # encoded_input = tokenizer([instruction + q for q in queries], padding=True, truncation=True, return_tensors='pt')

#     # Compute token embeddings
#     with torch.no_grad():
#         model_output = model(**encoded_input)
#         # Perform pooling. In this case, cls pooling.
#         sentence_embeddings = model_output[0][:, 0]
#     # normalize embeddings
#     sentence_embeddings = torch.nn.functional.normalize(sentence_embeddings, p=2, dim=1)
#     # print("Sentence embeddings shape:", sentence_embeddings.shape)
#     # print("Sentence embeddings:", sentence_embeddings)

#     return sentence_embeddings

# def zanurzenie_zdania(zdanie):
#     # Tokenize sentences
#     encoded_input = tokenizer(zdanie, padding=True, truncation=True, return_tensors='pt')
#     # for s2p(short query to long passage) retrieval task, add an instruction to query (not add instruction for passages)
#     # encoded_input = tokenizer([instruction + q for q in queries], padding=True, truncation=True, return_tensors='pt')

#     # Compute token embeddings
#     with torch.no_grad():
#         model_output = model(**encoded_input)
#         # Perform pooling. In this case, cls pooling.
#         sentence_embedding = model_output[0][:, 0]
#     # normalize embeddings
#     sentence_embedding = torch.nn.functional.normalize(sentence_embedding, p=2, dim=1)

#     return sentence_embedding

In [113]:
# treningowe_in_lista = treningowe["in"].tolist()
# treningowe_out_lista = treningowe["out"].tolist()

# print(len(treningowe_in_lista))
# print(treningowe_in_lista[0])
# print(treningowe_out_lista[0])

# zanurzenia_treningowe_in = zanurzenia_zdan(treningowe_in_lista)
# zanurzenia_treningowe_out = zanurzenia_zdan(treningowe_out_lista)

# print(zanurzenia_treningowe_in.shape)
# print(zanurzenia_treningowe_in[0])
# print(zanurzenia_treningowe_out[0])

### Tensory - reprezentacje pierwszych wersów wierszy treningowych.

In [114]:
x = []
for indeks_wersu_pierwszego in range(len(poczatki_treningowe_in)):
    poczatki = poczatki_treningowe_in
    konce = konce_treningowe_in
    tony = tony_treningowe_in
    niezerowe_poczatki = [p for p in poczatki[indeks_wersu_pierwszego] if p>0.0]
    poczatek_ostatniego_znaku = niezerowe_poczatki[len(niezerowe_poczatki)-1]
    koniec_ostatniego_znaku = konce[indeks_wersu_pierwszego][len(niezerowe_poczatki)-1]
    ton_ostatniego_znaku = tony[indeks_wersu_pierwszego][len(niezerowe_poczatki)-1]
    x.append(torch.cat(
        (
            # zanurzenia_treningowe_in[indeks_wersu_pierwszego],
            torch.from_numpy(poczatki_treningowe_in[indeks_wersu_pierwszego]),
            torch.from_numpy(konce_treningowe_in[indeks_wersu_pierwszego]),
            torch.from_numpy(tony_treningowe_in[indeks_wersu_pierwszego]),
            torch.from_numpy(numpy.array([len(niezerowe_poczatki)])),
            torch.from_numpy(numpy.array([poczatek_ostatniego_znaku])),
            torch.from_numpy(numpy.array([koniec_ostatniego_znaku])),
            torch.from_numpy(numpy.array([ton_ostatniego_znaku]))
        )
    ))
print(len(x))
print(x[0].shape)
print(x[0])

5959
torch.Size([109])
tensor([22,  9, 22, 17, 12,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,
         0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  3,
        16, 21,  2, 32,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,
         0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  3,  1,
         2,  3,  4,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,
         0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  5, 12, 32,
         4])


### Tensory - reprezentacje drugich wersów wierszy treningowych.

In [115]:
y = []
for indeks_wersu_pierwszego in range(len(poczatki_treningowe_out)):
    poczatki = poczatki_treningowe_out
    konce = konce_treningowe_out
    tony = tony_treningowe_out
    niezerowe_poczatki = [p for p in poczatki[indeks_wersu_pierwszego] if p>0.0]
    poczatek_ostatniego_znaku = niezerowe_poczatki[len(niezerowe_poczatki)-1]
    koniec_ostatniego_znaku = konce[indeks_wersu_pierwszego][len(niezerowe_poczatki)-1]
    ton_ostatniego_znaku = tony[indeks_wersu_pierwszego][len(niezerowe_poczatki)-1]
    y.append(
        torch.cat(
        (
            # zanurzenia_treningowe_out[indeks_wersu_pierwszego],
            torch.from_numpy(poczatki_treningowe_out[indeks_wersu_pierwszego]),
            torch.from_numpy(konce_treningowe_out[indeks_wersu_pierwszego]),
            torch.from_numpy(tony_treningowe_out[indeks_wersu_pierwszego]),
            torch.from_numpy(numpy.array([len(niezerowe_poczatki)])),
            torch.from_numpy(numpy.array([poczatek_ostatniego_znaku])),
            torch.from_numpy(numpy.array([koniec_ostatniego_znaku])),
            torch.from_numpy(numpy.array([ton_ostatniego_znaku]))
        )
    )
    )
print(len(y))
print(y[0].shape)
print(y[0])

5959
torch.Size([109])
tensor([13, 17, 21,  4,  8,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,
         0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0, 19,
        30,  4, 31, 12,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,
         0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  1,  3,
         4,  1,  2,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,
         0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  5,  8, 12,
         2])


## Wejście do sieci neuronowej.
### Odpowiadające sobie wersy i kilka losowo dobranych nieodpowiadających sobie wersów.

In [116]:
from random import sample
X = []
Y = []
for indeks_wersu_drugiego in range(len(x)):
    indeksy = sample(range(len(y)), 5)
    if indeks_wersu_drugiego not in indeksy:
        indeksy[0] = indeks_wersu_drugiego
    for k in indeksy:
        X.append(
            torch.cat(
                (x[indeks_wersu_drugiego], y[k])
            )
        )
        if indeks_wersu_drugiego==k:
            Y.append(1)
        else:
            Y.append(0)

print(len(X))
print(X[0])
print(len(Y))
print(Y[0])

29795
tensor([22,  9, 22, 17, 12,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,
         0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  3,
        16, 21,  2, 32,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,
         0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  3,  1,
         2,  3,  4,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,
         0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  5, 12, 32,
         4, 13, 17, 21,  4,  8,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,
         0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,
        19, 30,  4, 31, 12,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,
         0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  1,
         3,  4,  1,  2,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,
         0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  5,  8,
        12,  2])
29795
1


## Modele sklearn.

In [117]:
from sklearn.neural_network import MLPClassifier
klasyfikator = MLPClassifier()   # activation="tanh"

klasyfikator.fit(X, Y)

MLPClassifier()

In [118]:
from sklearn.neural_network import MLPRegressor
regresor = MLPRegressor()   # activation="tanh"

regresor.fit(X, Y)

MLPRegressor()

### Początki, końcówki i tony wierszy testowych.

In [119]:
print(len(testowe["in"]))
print(testowe["in"][0])
print(testowe["out"][0])

liczba_wejscia = 35

poczatki_testowe_in, konce_testowe_in, tony_testowe_in = poczatki_konce_tony_dla_zdan(testowe["in"], liczba_wejscia)
poczatki_testowe_out, konce_testowe_out, tony_testowe_out = poczatki_konce_tony_dla_zdan(testowe["out"], liczba_wejscia)

print(len(poczatki_testowe_in))
print(poczatki_testowe_in[0])
print(konce_testowe_in[0])
print(tony_testowe_in[0])
print(poczatki_testowe_out[0])
print(konce_testowe_out[0])
print(tony_testowe_out[0])

1490
林霭渐浓迷古寺
尘烟已远隐青山
1490
[ 8 22 12  7  3  9 21  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
  0  0  0  0  0  0  0  0  0  0  0]
[25 12 21 34  1  2  1  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
  0  0  0  0  0  0  0  0  0  0  0]
[2 3 4 2 2 3 4 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0]
[16 22 22 22 22 13 17  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
  0  0  0  0  0  0  0  0  0  0  0]
[24 21  1 23 25 32 20  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
  0  0  0  0  0  0  0  0  0  0  0]
[2 1 3 3 3 1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0]


### Zanurzenia BAAI wierszy testowych.

In [120]:
# testowe_in_lista = testowe["in"].tolist()
# testowe_out_lista = testowe["out"].tolist()

# print(len(testowe_in_lista))
# print(testowe_in_lista[0])
# print(testowe_out_lista[0])

# zanurzenia_testowe_in = zanurzenia_zdan(testowe_in_lista)
# zanurzenia_testowe_out = zanurzenia_zdan(testowe_out_lista)

# print(zanurzenia_testowe_in.shape)
# print(zanurzenia_testowe_in[0])
# print(zanurzenia_testowe_out[0])

### Tensory - reprezentacje pierwszych wersów wierszy testowych.

In [121]:
x_test = []
for indeks_wersu_pierwszego in range(len(poczatki_testowe_in)):
    poczatki = poczatki_testowe_in
    konce = konce_testowe_in
    tony = tony_testowe_in
    niezerowe_poczatki = [p for p in poczatki[indeks_wersu_pierwszego] if p>0.0]
    poczatek_ostatniego_znaku = niezerowe_poczatki[len(niezerowe_poczatki)-1]
    koniec_ostatniego_znaku = konce[indeks_wersu_pierwszego][len(niezerowe_poczatki)-1]
    ton_ostatniego_znaku = tony[indeks_wersu_pierwszego][len(niezerowe_poczatki)-1]
    x_test.append(torch.cat(
        (
            #zanurzenia_testowe_in[indeks_wersu_pierwszego],
            torch.from_numpy(poczatki_testowe_in[indeks_wersu_pierwszego]),
            torch.from_numpy(konce_testowe_in[indeks_wersu_pierwszego]),
            torch.from_numpy(tony_testowe_in[indeks_wersu_pierwszego]),
            torch.from_numpy(numpy.array([len(niezerowe_poczatki)])),
            torch.from_numpy(numpy.array([poczatek_ostatniego_znaku])),
            torch.from_numpy(numpy.array([koniec_ostatniego_znaku])),
            torch.from_numpy(numpy.array([ton_ostatniego_znaku]))
        )
    ))
print(len(x_test))
print(x_test[0].shape)
print(x_test[0])

1490
torch.Size([109])
tensor([ 8, 22, 12,  7,  3,  9, 21,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,
         0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0, 25,
        12, 21, 34,  1,  2,  1,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,
         0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  2,  3,
         4,  2,  2,  3,  4,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,
         0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  7, 21,  1,
         4])


### Tensory - reprezentacje drugich wersów wierszy testowych.

In [122]:
y_test = []
for indeks_wersu_pierwszego in range(len(poczatki_testowe_out)):
    poczatki = poczatki_testowe_out
    konce = konce_testowe_out
    tony = tony_testowe_out
    niezerowe_poczatki = [p for p in poczatki[indeks_wersu_pierwszego] if p>0.0]
    poczatek_ostatniego_znaku = niezerowe_poczatki[len(niezerowe_poczatki)-1]
    koniec_ostatniego_znaku = konce[indeks_wersu_pierwszego][len(niezerowe_poczatki)-1]
    ton_ostatniego_znaku = tony[indeks_wersu_pierwszego][len(niezerowe_poczatki)-1]
    y_test.append(
        torch.cat(
        (
            # zanurzenia_testowe_out[indeks_wersu_pierwszego],
            torch.from_numpy(poczatki_testowe_out[indeks_wersu_pierwszego]),
            torch.from_numpy(konce_testowe_out[indeks_wersu_pierwszego]),
            torch.from_numpy(tony_testowe_out[indeks_wersu_pierwszego]),
            torch.from_numpy(numpy.array([len(niezerowe_poczatki)])),
            torch.from_numpy(numpy.array([poczatek_ostatniego_znaku])),
            torch.from_numpy(numpy.array([koniec_ostatniego_znaku])),
            torch.from_numpy(numpy.array([ton_ostatniego_znaku]))
        )
    )
    )
print(len(y_test))
print(y_test[0].shape)
print(y_test[0])

1490
torch.Size([109])
tensor([16, 22, 22, 22, 22, 13, 17,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,
         0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0, 24,
        21,  1, 23, 25, 32, 20,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,
         0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  2,  1,
         3,  3,  3,  1,  1,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,
         0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  7, 17, 20,
         1])


## Wejście do sieci neuronowej.

In [123]:
X_test = []
Y_test = []
for indeks_wersu_drugiego in range(len(x_test)):
    indeksy = sample(range(len(y_test)), 5)
    if indeks_wersu_drugiego not in indeksy:
        indeksy[0] = indeks_wersu_drugiego
    for k in indeksy:
        X_test.append(
            torch.cat(
                (x_test[indeks_wersu_drugiego], y_test[k])
            )
        )
        if indeks_wersu_drugiego==k:
            Y_test.append(1)
        else:
            Y_test.append(0)

print(len(X_test))
print(X_test[0])
print(len(Y_test))
print(Y_test[0])

7450
tensor([ 8, 22, 12,  7,  3,  9, 21,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,
         0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0, 25,
        12, 21, 34,  1,  2,  1,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,
         0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  2,  3,
         4,  2,  2,  3,  4,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,
         0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  7, 21,  1,
         4, 16, 22, 22, 22, 22, 13, 17,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,
         0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,
        24, 21,  1, 23, 25, 32, 20,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,
         0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  2,
         1,  3,  3,  3,  1,  1,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,
         0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  7, 17,
        20,  1])
7450
1


## Przewidywania sieci neuronowych.

In [124]:
przewidywania_klasyfikatora = klasyfikator.predict(X_test)

In [125]:
przewidywania_regresora = regresor.predict(X_test)
print(numpy.min(przewidywania_regresora),numpy.max(przewidywania_regresora),numpy.mean(przewidywania_regresora),numpy.median(przewidywania_regresora))

-1.5850154355095964 1.513799312237276 0.20544654697588927 0.17125274897300372


### Dokładność na przygotowanych danych testowych.

In [126]:
### MLPClassifier

licznik = 0
mianownik = 0
for indeks_wersu_pierwszego in range(len(przewidywania_klasyfikatora)):
    mianownik+=1
    if przewidywania_klasyfikatora[indeks_wersu_pierwszego]==Y_test[indeks_wersu_pierwszego]:
        licznik+=1

print(licznik/mianownik*1.0)

0.8555704697986577


In [127]:
### MLPRegressor

# Dopasowanie powyżej 0.5
licznik = 0
mianownik = 0
for indeks_wersu_pierwszego in range(len(przewidywania_regresora)):
    mianownik+=1
    if Y_test[indeks_wersu_pierwszego]==1 and przewidywania_regresora[indeks_wersu_pierwszego]>0.5:
        licznik+=1
    elif Y_test[indeks_wersu_pierwszego]==0 and przewidywania_regresora[indeks_wersu_pierwszego]<0.5:
        licznik+=1

print(licznik/mianownik*1.0)

#Dopasowanie powyżej 0.9
licznik = 0
mianownik = 0
for indeks_wersu_pierwszego in range(len(przewidywania_regresora)):
    mianownik+=1
    if Y_test[indeks_wersu_pierwszego]==1 and przewidywania_regresora[indeks_wersu_pierwszego]>0.9:
        licznik+=1
    elif Y_test[indeks_wersu_pierwszego]==0 and przewidywania_regresora[indeks_wersu_pierwszego]<0.9:
        licznik+=1

print(licznik/mianownik*1.0)

0.8377181208053691
0.8087248322147651


## Metryka oceniająca proponowanie przez model drugiego wersu.
### Jeżeli wśród propozycji nie ma spodziewanego poprawnego wersu, metryka przyjmuje minimalną wartość 0,0.
### Im mniej błędnych propozycji , tym wyższy wynik metryki.
### Jeżeli model proponuje tylko jeden wers i jest on poprawny, metryka przyjmuje maksymalną wartość 1,0.

In [128]:
def jagosz_score(spodziewany_wers,proponowane_wersy):
    if spodziewany_wers in proponowane_wersy:
        licznik = 1
    else:
        licznik = 0
    mianownik = len(proponowane_wersy)
    if mianownik==0:
        mianownik=1
    return licznik/mianownik*1.0

### Wersja metryki dla całego zbioru.

In [129]:
def jagosz_score_dla_zbioru(krotki):
    licznik = 0
    mianownik = 0

    for k in krotki:
        spodziewany_wers = k[0]
        proponowane_wersy = k[1]
        if spodziewany_wers in proponowane_wersy:
            licznik += 1
        mianownik += len(proponowane_wersy)

    if mianownik==0:
        return 0
    else:
        return licznik/mianownik*1.0

In [130]:
wybrane_dane_testowe = sample(range(len(x_test)),10)

## MLPClassifier
### Proponuje wszystkie wersy, dla których ocena modelu to 1.

In [131]:
for indeks_wersu_pierwszego in wybrane_dane_testowe:
    wers_pierwszy = testowe["in"][indeks_wersu_pierwszego]
    print("wers pierwszy:\t\t", wers_pierwszy)
    poprawny_wers_drugi = testowe["out"][indeks_wersu_pierwszego]
    print("poprawny wers drugi:\t", poprawny_wers_drugi)
    print()

    reprezentacja_wersu_pierwszego = x_test[indeks_wersu_pierwszego]
    mozliwe_indeksy_wersu_drugiego = []
    for indeks_wersu_drugiego in range(len(y_test)):
        reprezentacja_wersu_drugiego = y_test[indeks_wersu_drugiego]
        wejscie_do_MLP = torch.cat((reprezentacja_wersu_pierwszego, reprezentacja_wersu_drugiego))
        if klasyfikator.predict([wejscie_do_MLP])[0] == 1:
            mozliwe_indeksy_wersu_drugiego.append(indeks_wersu_drugiego)

    proponowane_wersy = [testowe["out"][i] for i in mozliwe_indeksy_wersu_drugiego]
    print("proponowane drugie wersy:", proponowane_wersy)
    print("czy poprawny wers jest pośród proponowanych wersów?:", poprawny_wers_drugi in proponowane_wersy)
    print("liczba proponowanych wersów:", len(proponowane_wersy))
    print()

    print("wynik przyjętej metryki:", jagosz_score(poprawny_wers_drugi, proponowane_wersy))
    print()
    print("-"*50)
    print()

wers pierwszy:		 仁义自修君子安我
poprawny wers drugi:	 诗礼之教家人利贞

proponowane drugie wersy: ['丰碑万古纪殊勋', '情牵大地春满人间', '珠圆玉润入口皆甜', '德行梦笔开盛世新篇', '柔水月光披野地天穹', '闲耽笔墨自从容', '一湾碧水日如金', '浮沉历尽许由谁', '人情世故亦须明', '三番顾茅庐皇叔牵龙', '春光入户户新幸福多', '花明柳媚湖上长春', '调一湖春色染绿江淮', '发者斗芳梅葩早帅焉', '一联争首榜元眼花胪', '深恩彻骨万代常萦', '堤前柳浪露春光', '湖山叠韵入我诗囊', '辞雄子建赋拟相如', '行廉拒腐执法如山', '国运弥盛史弥远', '瑞通阆苑琼楼兴百轩', '苗兴汉夏望族振乾坤', '砖雕雕壁画砖马腾空', '歌酣万户九域报长春', '千幅对联红透时光', '赋浓夏盛寓秋实', '东床配西席不是东西', '飞鸿远浦一时惊', '就门外汉示不二门', '天心阁阁内鸽鸽飞阁不飞', '捉刀李白斩斯文', '桨声翻学海海载苦舟', '月光如户窥佳人', '小康致富富人间', '直播日照时时精彩', '共赏芦溪水高下相倾', '喜传桃谷峪马叫人欢', '满腔忧愤铸诗魂', '荷描夏画日钤章', '小桃几树鸟啼红', '五光十色文字之华', '柳垂水面翠溶南北风', '伟雄心志白鹤相知', '小金龙瑞雪兆丰年', '松风竹韵多抒情', '当辨忠奸岂可负全民', '心中无欲不争春', '樽彝错杂古道犹存', '诗礼之教家人利贞', '出门去白面书生', '中古生华易古往冬', '攀龙附凤欲攀彩凤缘', '地连南北日星恒久晖', '吸烟无益肺摧残', '蔼峰亦寄诗仙情', '杯中寂寞不曾空', '油田崛起为生产护航', '综一代典成一家言', '辩雕春囿德莹秋天', '碧峰犹冷寺前春', '微言明义苦谏纠偏', '尘凡皆妄昧贪嗔痴愚', '草逢蓬室至家中', '平野百里高山九重', '诗篇避俗不酬人', '官吏非全力吏全力官', '利人始是大修行', '鸣钟食鼎甘田土之出', '手携一集质于通人', '方塘九夏溢荷香', '扬风遗泽仁厚人家', '风中落叶泣无声', '雅情雅韵仙客有约', '开枰先弃是非心', '陈天保颂代地道终', '飞腾雅典

## MLPRegressor
### Proponuje wszystkie wersy, dla których ocena modelu jest większa niż 0,9.

In [132]:
for indeks_wersu_pierwszego in wybrane_dane_testowe:
    wers_pierwszy = testowe["in"][indeks_wersu_pierwszego]
    print("wers pierwszy:\t\t", wers_pierwszy)
    poprawny_wers_drugi = testowe["out"][indeks_wersu_pierwszego]
    print("poprawny wers drugi:\t", poprawny_wers_drugi)
    print()

    reprezentacja_wersu_pierwszego = x_test[indeks_wersu_pierwszego]
    mozliwe_indeksy_wersu_drugiego = []
    wartosci_przewidywan_wersu_drugiego = []
    for indeks_wersu_drugiego in range(len(y_test)):
        reprezentacja_wersu_drugiego = y_test[indeks_wersu_drugiego]
        wejscie_do_MLP = torch.cat((reprezentacja_wersu_pierwszego, reprezentacja_wersu_drugiego))
        mozliwe_indeksy_wersu_drugiego.append(indeks_wersu_drugiego)
        wartosci_przewidywan_wersu_drugiego.append(regresor.predict([wejscie_do_MLP])[0])

    pom_df = pandas.DataFrame({"indeks":mozliwe_indeksy_wersu_drugiego,"wartosc":wartosci_przewidywan_wersu_drugiego})
    proponowane_wersy = [testowe["out"][i] for i in pom_df["indeks"] if pom_df["wartosc"][i]>=0.9]

    print("proponowane drugie wersy:", proponowane_wersy)
    print("czy poprawny wers jest pośród proponowanych wersów?:", poprawny_wers_drugi in proponowane_wersy)
    print("liczba proponowanych wersów:", len(proponowane_wersy))
    print()

    print("wynik przyjętej metryki:", jagosz_score(poprawny_wers_drugi, proponowane_wersy))
    if (len(proponowane_wersy)<1 or len(proponowane_wersy)>5):
        print("wyjaśnienie - największe wartości przewidywań")
        print(pom_df.nlargest(len(proponowane_wersy)+1, "wartosc"))
    print()
    print("-"*50)
    print()

wers pierwszy:		 仁义自修君子安我
poprawny wers drugi:	 诗礼之教家人利贞

proponowane drugie wersy: []
czy poprawny wers jest pośród proponowanych wersów?: False
liczba proponowanych wersów: 0

wynik przyjętej metryki: 0.0
wyjaśnienie - największe wartości przewidywań
     indeks  wartosc
275     275    0.698

--------------------------------------------------

wers pierwszy:		 雪落千山静
poprawny wers drugi:	 冰封万水寒

proponowane drugie wersy: ['思量枕席功夫']
czy poprawny wers jest pośród proponowanych wersów?: False
liczba proponowanych wersów: 1

wynik przyjętej metryki: 0.0

--------------------------------------------------

wers pierwszy:		 莫漫三槐羡王自
poprawny wers drugi:	 须先百忍学张公

proponowane drugie wersy: []
czy poprawny wers jest pośród proponowanych wersów?: False
liczba proponowanych wersów: 0

wynik przyjętej metryki: 0.0
wyjaśnienie - największe wartości przewidywań
     indeks   wartosc
275     275  0.662909

--------------------------------------------------

wers pierwszy:		 到此酒垆应更好
poprawny wers dru

### Przyjęta metryka dla 1/100 zbioru testowego.

In [133]:
krotki = []
czesc_zbioru_testowego, _ = train_test_split(x_test,test_size=0.95,random_state=42)

for indeks_wersu_pierwszego in range(len(czesc_zbioru_testowego)):
    wers_pierwszy = testowe["in"][indeks_wersu_pierwszego]
    poprawny_wers_drugi = testowe["out"][indeks_wersu_pierwszego]

    reprezentacja_wersu_pierwszego = x_test[indeks_wersu_pierwszego]
    mozliwe_indeksy_wersu_drugiego = []
    wartosci_przewidywan_wersu_drugiego = []
    for indeks_wersu_drugiego in range(len(y_test)):
        reprezentacja_wersu_drugiego = y_test[indeks_wersu_drugiego]
        wejscie_do_MLP = torch.cat((reprezentacja_wersu_pierwszego, reprezentacja_wersu_drugiego))
        mozliwe_indeksy_wersu_drugiego.append(indeks_wersu_drugiego)
        wartosci_przewidywan_wersu_drugiego.append(regresor.predict([wejscie_do_MLP])[0])

    pom_df = pandas.DataFrame({"indeks":mozliwe_indeksy_wersu_drugiego,"wartosc":wartosci_przewidywan_wersu_drugiego})
    proponowane_wersy = [testowe["out"][i] for i in pom_df["indeks"] if pom_df["wartosc"][i]>=0.9]

    krotki.append((poprawny_wers_drugi,proponowane_wersy))

print(jagosz_score_dla_zbioru(krotki))

0.008174386920980926


### Średnia metryk dla 1/100 zbioru testowego.

In [134]:
jagosz_scores=[]
for indeks_wersu_pierwszego in range(len(czesc_zbioru_testowego)):
    wers_pierwszy = testowe["in"][indeks_wersu_pierwszego]
    poprawny_wers_drugi = testowe["out"][indeks_wersu_pierwszego]

    reprezentacja_wersu_pierwszego = x_test[indeks_wersu_pierwszego]
    mozliwe_indeksy_wersu_drugiego = []
    wartosci_przewidywan_wersu_drugiego = []
    for indeks_wersu_drugiego in range(len(y_test)):
        reprezentacja_wersu_drugiego = y_test[indeks_wersu_drugiego]
        wejscie_do_MLP = torch.cat((reprezentacja_wersu_pierwszego, reprezentacja_wersu_drugiego))
        mozliwe_indeksy_wersu_drugiego.append(indeks_wersu_drugiego)
        wartosci_przewidywan_wersu_drugiego.append(regresor.predict([wejscie_do_MLP])[0])

    pom_df = pandas.DataFrame({"indeks":mozliwe_indeksy_wersu_drugiego,"wartosc":wartosci_przewidywan_wersu_drugiego})
    proponowane_wersy = [testowe["out"][i] for i in pom_df["indeks"] if pom_df["wartosc"][i]>=0.9]

    jagosz_scores.append(jagosz_score(poprawny_wers_drugi,proponowane_wersy))

print(numpy.mean(jagosz_scores))

0.004512548262548263


In [135]:
print(len(czesc_zbioru_testowego))

74
